In [1]:
from src.tools.ploty_api import *
import chart_studio.plotly as py
import chart_studio.tools as tls

import cufflinks as cf
import numpy as np
import pandas as pd
import networkx as nx
from fa2 import ForceAtlas2
import seaborn as sns


import plotly.express as px
import plotly.graph_objects as go

%matplotlib inline

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

init_notebook_mode(connected=True)
cf.go_offline()

# Poltical Networks

### Create random graph

In [24]:
df_Twitter_Handels = pd.read_csv('../Data/Processed/Twitter_Handles.csv')
G = nx.read_gpickle('../models/directed_follow_graph.pickle')
G_u = nx.read_gpickle('../models/undirected_follow_graph.pickle')

#### Get positions using force atlas 

In [25]:
forceatlas2 = ForceAtlas2(
    # Behavior alternatives
    outboundAttractionDistribution=False,  # Dissuade hubs
    edgeWeightInfluence = 0.5, # Performance

    # Performance
    jitterTolerance=0.2,  # Tolerance
    barnesHutOptimize=True,
    barnesHutTheta=0.6,

    # Tuning
    scalingRatio=5.0,
    gravity=1.0,

    # Log
    verbose=True
)

# Calculate positions
positions = forceatlas2.forceatlas2_networkx_layout(G_u, pos=None, iterations=2500)

100%|██████████| 2500/2500 [00:25<00:00, 96.91it/s]BarnesHut Approximation  took  3.41  seconds
Repulsion forces  took  18.51  seconds
Gravitational forces  took  0.11  seconds
Attraction forces  took  2.67  seconds
AdjustSpeedAndApplyForces step  took  0.41  seconds



In [26]:
node_x = []
node_y = []
parties = []
nodes = []

for node, party in nx.get_node_attributes(G_u, 'Party').items():
    x, y = positions[ node ]
    node_x.append(x)
    node_y.append(y)
    parties.append(party)
    nodes.append(node)

df_network = pd.DataFrame({
    'x' : node_x,
    'y' : node_y,
    'party' : parties,
    'Twitter' : nodes,
})

df_degree = pd.DataFrame({
    'Twitter' : [politican for politican, degree in G.in_degree],
    'in_degree' :  [degree for politican, degree in G.in_degree],
    'out_degree' :  [degree for politican, degree in G.out_degree]
})
df_degree['degree'] = df_degree['in_degree'] + df_degree['out_degree' ]


# Merge twitter handle
df_network = df_network.merge(
    df_Twitter_Handels[['State', 'Type', 'Party', 'Twitter', 'Name']], 
    how = 'left',
    on = 'Twitter'
)
# Merge degree
df_network = df_network.merge(
    df_degree, 
    how = 'left',
    on = 'Twitter'
)

In [27]:
df_network

x           y       party          Twitter State  \
0    -885.951626 -133.799802  Republican        JeffFlake    AZ   
1    -915.531379  351.190835  Republican      DarrellIssa    CA   
2   -1611.306740  715.256480  Republican  DanaRohrabacher    CA   
3   -1175.348620  788.322176  Republican       RepEdRoyce    CA   
4    -786.176200  815.575633  Republican  RepDavidValadao    CA   
..           ...         ...         ...              ...   ...   
590 -1631.036562 -290.739339  Republican     TomTiffanyWI    WI   
591  -627.789620 -401.959895  Republican      SenatorEnzi    WY   
592  -883.022332 -436.697581  Republican  SenJohnBarrasso    WY   
593 -1621.815867   24.755203  Republican       Liz_Cheney    WY   
594 -1891.067936   47.889816  Republican  realDonaldTrump   NaN   

               Type Party              Name  in_degree  out_degree  degree  
0           Senator     R        Jeff Flake        162          11     173  
1    Representative     R      Darrell Issa        207         290     497  
2    Representative     R  Dana Rohrabacher         96           4     100  
3    Representative     R          Ed Royce        162         106     268  
4    Representative     R     David Valadao        115          53     168  
..              ...   ...               ...        ...         ...     ...  
590  Representative     R    Thomas Tiffany          3           4       7  
591         Senator     R         Mike Enzi        128         105     233  
592         Senator     R     John Barrasso        154          69     223  
593  Representative     R        Liz Cheney         61          20      81  
594           POTUS     R   Donald J. Trump        314           2     316  

[595 rows x 11 columns]

### Create Edges

In [28]:
# Edge colors
def select_edges(Party1, Party2):
    # Orange between two republican
    if Party1 == 'Republican' and Party2 == 'Republican':
        edge_type = 'Republican' 
    
    # Cyan between two democrates
    elif Party1 == 'Democrat' and Party2 == 'Democrat':
        edge_type = 'Democrat' 
    
    # Gray when connected to an independent
    elif Party1 == 'Independent' or Party2 == 'Independent':
        edge_type = 'Independent' 

    # Yellow when connected to a liberal
    elif Party1 == 'Libertarian' or Party2 == 'Libertarian':
        edge_type = "Libertarian" 
    
    # Purple elsewhere (between democrat and republican)
    else:
        edge_type = 'Other' 
        
    return edge_type 


def color_edges(G, positions, edges, color, edge_name):

    edge_x = []
    edge_y = []
    edge_text = []
    for edge in edges:
        x0, y0 = positions[ edge[0] ]
        x1, y1 = positions[ edge[1] ]
        edge_x.append(x0)
        edge_x.append(x1)
        edge_x.append(None)
        edge_y.append(y0)
        edge_y.append(y1)
        edge_y.append(None)
        edge_text.append(edge[0])


    edge_trace = go.Scattergl(
        x=edge_x, 
        y=edge_y,
        line=dict(width=0.7, color=color),
        opacity = 0.3,
        name=edge_name,
        showlegend=True,
        mode='lines',
        hoverinfo='skip',
        hovertemplate=None
    )
    
    return edge_trace


In [29]:
# Get add edges colors
edge_types = {
    (f, t) :  select_edges(
        *(nx.get_node_attributes(G_u, 'Party')[f], nx.get_node_attributes(G_u, 'Party')[t])
    )
    for f, t in G_u.edges
}

parties = ['Republican', 'Democrat', 'Independent', 'Libertarian', 'Other']
colors = ['#ff7f0e', '#17becf', '#7f7f7f', '#FED105', '#9467bd']
edge_names = ['Rep-Rep', 'Dem-Dem', 'Lib-Any', 'Ind-Any', 'Rep-Dem']
edge_traces = []
for party, color, edge_name in zip(parties, colors, edge_names):
    selected_edges = [node_pair for node_pair, edge_type in edge_types.items() if edge_type == party]

    edge_traces.append(
        color_edges(
            G = G_u,
            positions = positions,
            edges = selected_edges,
            color = color,
            edge_name = edge_name
        )
    )


### Create nodes 

In [30]:
node_x = []
node_y = []
for node in G_u.nodes():
    x, y = positions[ node ]
    node_x.append(x)
    node_y.append(y)

In [31]:
# Dictionary with parties and colors
color_dict = {"Democrat": "#0015BC", "Republican": "#DE0100", 'Independent': "#181818", 'Libertarian': "#FED105"}

In [32]:
marker_dict = {'Representative': 5, 'Senator': 14, 'POTUS': 17}

In [33]:
df_network.head()

x           y       party          Twitter State            Type  \
0  -885.951626 -133.799802  Republican        JeffFlake    AZ         Senator   
1  -915.531379  351.190835  Republican      DarrellIssa    CA  Representative   
2 -1611.306740  715.256480  Republican  DanaRohrabacher    CA  Representative   
3 -1175.348620  788.322176  Republican       RepEdRoyce    CA  Representative   
4  -786.176200  815.575633  Republican  RepDavidValadao    CA  Representative   

  Party              Name  in_degree  out_degree  degree  
0     R        Jeff Flake        162          11     173  
1     R      Darrell Issa        207         290     497  
2     R  Dana Rohrabacher         96           4     100  
3     R          Ed Royce        162         106     268  
4     R     David Valadao        115          53     168

In [34]:
node_traces = []
for party in df_network['party'].unique():

    for congress_type in  df_network['Type'].unique():
        df_tmp = df_network[(df_network['party'] == party) & (df_network['Type'] == congress_type)]
        node_texts = [f"{name}: {degree}" for name, degree in zip(df_tmp.Name.values, df_tmp.degree)]
        
        hovertemplates = [
                f'<b>Name: </b>{Name}<br><b>State: </b>{State}<br><b>Rule: </b>{Type}<br><b>Party: </b>{party}<br><b>In-degree: </b>{in_degree}<br><b>Out-degree: </b>{out_degree}<extra></extra>'
            for Name, State, Type, in_degree, out_degree in 
            zip(df_tmp['Name'], df_tmp['State'], df_tmp['Type'],df_tmp['in_degree'], df_tmp['out_degree'])
        ]

        node_trace = go.Scattergl(
            x = df_tmp['x'].values, 
            y = df_tmp['y'].values,
            marker_color = color_dict[party],
            name = party + ': ' + str(congress_type),
            mode = 'markers',
            hoverinfo = 'text',
            marker = dict(
                size = 5+(df_tmp['degree'].values)/12.5,
                opacity = 0.6,
                line_width=1
            ),
            marker_symbol = marker_dict[congress_type],
            hovertemplate = hovertemplates,
            #text = node_texts
        )
        node_traces.append(node_trace)

Color Node Points

In [35]:
## https://stackoverflow.com/questions/58278444/how-do-i-control-which-trace-plots-on-top-with-plotly

fig = go.Figure(
    data = [*edge_traces, *node_traces],
    layout=go.Layout(
        clickmode = 'select+event',
        title='Network graph of Twitter Followers',
        titlefont_size=16,
        showlegend=True,
        hovermode='y unified',
        #hovermode= False,
        #hovermode='closest',
        margin=dict(b=5,l=5,r=5,t=40),
        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)
    )
)

#*edge_traces
fig.write_html(
    file = "../web_app/plotly_files/follower_graph.html", 
    full_html = False,
    include_plotlyjs='cdn'
)
fig